In [1]:
import sys, time, random, math, cv2
import numpy as np
from matplotlib import pyplot as plt

sys.path.insert(0, '../src')
from robot import Robot

In [2]:
def pre_process_image(resolution, image):
    img = np.array(image,dtype=np.uint8)
    img.resize([resolution[1],resolution[0],3])
    
    cv2.imwrite('vision'+'.png',cv2.flip(img, 0))
    
    return cv2.flip(img, 0)

def apply_mask_by_color(image):
    hsv = cv2.cvtColor(image, cv2.COLOR_BGR2HSV)
    # define range of blue color in HSV
    lower_blue = np.array([110,50,50])
    upper_blue = np.array([130,255,255])
    
    # Threshold the HSV image to get only blue colors
    mask = cv2.inRange(hsv, lower_blue, upper_blue)
    
    # Bitwise-AND mask and original image
    return cv2.bitwise_and(image,image, mask= mask)

def calculate_center(image):
    cv2.imwrite('masked'+'.png',image)
    # convert image to grayscale image
    gray_image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY) 
    # convert the grayscale image to binary image
    ret,thresh = cv2.threshold(gray_image,10,255, cv2.THRESH_BINARY)
    
    cv2.imwrite('thresh'+'.png',thresh)
    
    img, contours, hierarchy = cv2.findContours(thresh,cv2.RETR_TREE,cv2.CHAIN_APPROX_SIMPLE)
    maximo = 0
    cmax = None
    for c in contours:
        area = cv2.contourArea(c)
        if area > maximo:
            maximo = area
            cmax = c
        
    # calculate moments for each contour
    M = cv2.moments(cmax)
    if(M["m00"] != 0 ):
        # calculate x,y coordinate of center
        cX = int(M["m10"] / M["m00"])
        cY = int(M["m01"] / M["m00"])

        cv2.circle(image, (cX, cY), 5, (255, 255, 255), -1)
        cv2.putText(image, "center", (cX - 25, cY - 25),cv2.FONT_HERSHEY_SIMPLEX, 0.5, (255, 255, 255), 2)

        # display the image
        cv2.imwrite('door'+'.png',image)
        return cX, cY, True
    
    return 0, 0, False

In [3]:
def laser_sensors(laser, c_position, gamma, label):
    x = []
    y = []
    
    rotation_matrix = np.matrix([[math.cos(gamma), -math.sin(gamma)], [math.sin(gamma), math.cos(gamma)]])
    for i in range(0, len(laser), 3):
        robot_position = np.matrix([[c_position[0]], [c_position[1]]])
        translation_matrix =  np.matrix([[laser[i]], [laser[i+1]]])
        T = np.matmul(rotation_matrix, translation_matrix)
        final_result = np.add(T, robot_position)
        x.append(final_result.item((0, 0)))
        y.append(final_result.item((1, 0)))
    plt.plot(x, y, label)

def update_map_gt():
    c_position = robot.get_current_position()
    c_orientation = robot.get_current_orientation()[2]
    laser = robot.read_laser()
    plt.figure(1)
    print(c_orientation)
    laser_sensors(laser, c_position, c_orientation, 'b.')
    plt.savefig('map_gt'+'.png')

def update_map_odometry(o_position, orientation):
    laser = robot.read_laser()
    plt.figure(2)
    print(orientation)
    laser_sensors(laser, o_position, orientation, 'r.')
    plt.savefig('map_odometry'+'.png')

def update_map(o_position, orientation):
    update_map_gt()
    update_map_odometry(o_position, orientation)

In [4]:
def front_sensors_move(dist, vel):
    vLeft = vRight = defaultVelocity
    if (dist[3] < noDetectionDist or dist[4] < noDetectionDist):
        side = random.randint(0,1)
        if (dist[2] < noDetectionDistDiag and dist[5] > noDetectionDistDiag):
            side = 0
        elif (dist[5] < noDetectionDistDiag and dist[2] > noDetectionDistDiag):
            side = 1
        elif (dist[2] < noDetectionDistDiag and dist[5] < noDetectionDistDiag):
            distance = robot.read_ultrassonic_sensors()
            if (distance[2] < noDetectionDistDiag or distance[5] < noDetectionDistDiag or distance[1] < noDetectionDistDiag or distance[6] < noDetectionDistDiag):
                return[-defaultVelocity, -defaultVelocity]
        if (side != 0):
            distance = robot.read_ultrassonic_sensors()
            if (distance[3] < noDetectionDist or distance[4] < noDetectionDist):
                return [-(defaultVelocity)/2, defaultVelocity/2]
        else:
            distance = robot.read_ultrassonic_sensors()
            if (distance[3] < noDetectionDist or distance[4] < noDetectionDist):
                return [defaultVelocity/2, -defaultVelocity/2]
    return [vLeft, vRight]

def walk(left_velocity, right_velocity, time_to_walk):
    robot.set_left_velocity(left_velocity)
    robot.set_right_velocity(right_velocity)  
    time.sleep(time_to_walk)


def enter_door(position, orientation):
    resolution, image = robot.read_vision_sensor()
    aux = resolution[0]/2
    image = pre_process_image(resolution, image)
    door = apply_mask_by_color(image)
    X,Y,isCenter = calculate_center(door)
    X += 5
    
    if (isCenter):
        while isCenter and abs(X - aux) > 5:
            if(X < aux):
                robot.set_left_velocity(-0.05)
                robot.set_right_velocity(0.05)

            elif(X >= aux):
                robot.set_left_velocity(0.05)
                robot.set_right_velocity(-0.05)
                
            _, image = robot.read_vision_sensor()
            image = pre_process_image(resolution, image)
            door = apply_mask_by_color(image)
            X,Y,isCenter = calculate_center(door)
            X += 5
        if not isCenter:
            return
    
        us_distances = robot.read_ultrassonic_sensors()
        dist_front = min(us_distances[3], us_distances[4])
        while (dist_front > 0.3):
            robot.set_left_velocity(min(defaultVelocity, dist_front))
            robot.set_right_velocity(min(defaultVelocity, dist_front))
            us_distances = robot.read_ultrassonic_sensors()
            dist_front = min(us_distances[3], us_distances[4])
            
        while (dist_front < 7):
            robot.set_left_velocity(0.3)
            robot.set_right_velocity(-0.3)
            us_distances = robot.read_ultrassonic_sensors()
            dist_front = min(us_distances[3], us_distances[4])
        time.sleep(0.5)
        
        walk(defaultVelocity, defaultVelocity, 15)
        update_map(position, orientation)
        
        walk(1, -1, 4)
        update_map(position, orientation)

        walk(-1, 1, 8)
        update_map(position, orientation)
        
        walk(1, -1, 4)
        
        walk(-defaultVelocity, -defaultVelocity, 20)
        walk(2, -2, 2)


In [5]:
def calculate_delta(begin, end, spinOrient):
    if math.isclose(float(end), float(begin), abs_tol=0.00001):
        return 0
    end = (limit + end) % limit
    begin = (limit + begin) % limit

    ans = abs(end - begin)
    if spinOrient:
        if begin < end:
            return limit - ans
        return ans
    if begin > end:
        return limit - ans
    return ans

def calculate_speed(time, clockwiseSpin, lastEncoder, motorHandle):
    encoder = robot.get_joint_position(motorHandle)
    delta = calculate_delta(lastEncoder, encoder, clockwiseSpin)
    
    lastEncoder = encoder
    if delta > math.pi:
        delta = (2 * math.pi) - delta
        clockwiseSpin = not clockwiseSpin
    
    speed = 0.0975 * (delta/time)
    if(clockwiseSpin):
        return -speed, clockwiseSpin, lastEncoder
    
    return speed, clockwiseSpin, lastEncoder

def to180Universe(alpha):
    alpha = alpha % (2 * math.pi)
    if alpha > math.pi:
        return alpha - (2 * math.pi)
    return alpha

def to360Universe(alpha):
    if alpha < 0:
        return (2 * math.pi) + alpha
    return alpha

def add_angle(alpha, beta):
    angle = to360Universe(alpha) + to360Universe(beta)
    return to180Universe(angle)

def new_position(alpha, x, y):
    global lastTime
    global lastEncoderL, lastEncoderR
    global clockwiseSpinL, clockwiseSpinR
    
    now = time.time()
    dtime = now-lastTime
    lastTime = now
    
    vL, clockwiseSpinL, lastEncoderL = calculate_speed(dtime, clockwiseSpinL, lastEncoderL, 'left')
    vR, clockwiseSpinR, lastEncoderR = calculate_speed(dtime, clockwiseSpinR, lastEncoderR, 'right')
    
    w = (vR-vL)/0.36205
    v = (vR + vL)/2.0
    
    dAlpha = w*dtime
    dL = vL*dtime
    dR = vR*dtime
    dM = (dL+dR)/2.0
    dX = dM*math.cos(add_angle(alpha, dAlpha/2.0))
    dY = dM*math.sin(add_angle(alpha, dAlpha/2.0))
    return x+dX, y+dY, add_angle(alpha, dAlpha)

def plot_odometry_vs_GT(path, path_odometry):
    _, ax = plt.subplots(figsize=(9, 9))
    ax.plot(path_odometry[:,0], path_odometry[:,1], label = 'Odometry')
    ax.plot(path[:,0], path[:,1], label = 'Ground Truth')
    ax.grid(True)
    ax.legend(loc='best')
    plt.xlabel("x")
    plt.ylabel("y")
    plt.title('Odometry x Ground Truth')
    plt.savefig('odometry'+'.png') 
#     plt.show()

In [6]:
class GoToGoalPID():
    epsilonA = 25
    KpA = 1.5
    KiA = KpA / 10.0
    KdA = KpA * 5
    epsilonP = 0.01
    KpP = 0.7
    KdP = KpP * 5
    
    def __init__(self):
        self.errorA = self.epsilonA
        self.oldErrorA = 0
        self.accErrorA = 0
        self.errorP = self.epsilonP
        self.oldErrorP = 0
    
    def calcule_norm_angle(self, angle):
        return angle % (2*math.pi)

    def calcule_x1_y1_angle(self, position, angle, goal):
        x1 = position[0] - goal[0]
        y1 = position[1] - goal[1]
        angle = self.calcule_norm_angle(angle)
        return x1, y1, angle

    def calcule_errorA(self, position, angle, goal):
        x1, y1, angle = self.calcule_x1_y1_angle(position, angle, goal)
        goalAngle = self.calcule_norm_angle(math.pi + math.atan2(y1, x1))
        self.errorA = math.atan2(math.sin(goalAngle-angle), math.cos(goalAngle-angle))

    def calcule_go_to_position(self, position, angle, goal):
        x1, y1, angle = self.calcule_x1_y1_angle(position, angle, goal)
        goalAngle = self.calcule_norm_angle(math.pi + math.atan2(y1, x1))
        deltaA = math.degrees(math.atan2(math.sin(goalAngle-angle), math.cos(goalAngle-angle)))
        sig = -1 if abs(deltaA) > 100 else 1

        self.errorP = sig * math.sqrt( ((goal[0]-position[0])**2) + ((goal[1]-position[1])**2) )
        diffErrorP = self.errorP - self.oldErrorP
        u = (self.KpP * self.errorP) + (self.KdP * diffErrorP)
        self.oldErrorP = self.errorP
        return [u,u]


    def calcule_go_to_angle(self, position, angle, goal):
        self.calcule_errorA(position, angle, goal)
        self.accErrorA = self.accErrorA + self.errorA
        diffErrorA = self.errorA - self.oldErrorA
        u = (self.KpA * self.errorA) + (self.KiA * self.accErrorA) + (self.KdA * diffErrorA)
        self.oldErrorA = self.errorA
        return [u,-u]


    def go_to_goal_PID(self, position, angle, goal):
        if abs(math.degrees(self.errorA)) < self.epsilonA:
            self.calcule_errorA(position, angle, goal)
            if abs(self.errorP) >= self.epsilonP:
                return self.calcule_go_to_position(position, angle, goal)
            else:
                return [0,0]
        else:
            return self.calcule_go_to_angle(position, angle, goal)



In [ ]:
noDetectionDist = 0.7
defaultVelocity = 1
noDetectionDistDiag = 0.4

robot = Robot()

limit = 2*math.pi
lastTime=time.time()
clockwiseSpinL = False
clockwiseSpinR = False
lastEncoderL = robot.get_joint_position('left')
lastEncoderR = robot.get_joint_position('right')

position = robot.get_current_position()
orientation = robot.get_current_orientation()

alpha = orientation[2]
x = position[0]
y = position[1]


goal = np.array([2.12, -3.82])
goToGoalPID = GoToGoalPID()

path = []
path_odometry = []

while(robot.get_connection_status() != -1):
    
    angle = robot.get_current_orientation()[2]
    position = robot.get_current_position()    
    
    vGoToPID = goToGoalPID.go_to_goal_PID(position, angle, goal)
    
    robot.set_left_velocity(vGoToPID[1] * 0.1)
    robot.set_right_velocity(vGoToPID[0] * 0.1)
    print(vGoToPID)
    
#     us_distances = robot.read_ultrassonic_sensors()
#     vel = front_sensors_move(us_distances[:8], defaultVelocity)
#     walk(vel[0], vel[1], 3)
#     walk(0, 0, 0)
    
#     update_map([x,y,0], alpha)
        
#     enter_door([x,y,0], alpha)
    
    # Odometria
#     x, y, alpha = new_position(alpha, x, y)
#     path.append([-position[1], position[0]])
#     path_odometry.append([-y, x])
    

Connected to remoteApi server.
 Pioneer_p3dx_ultrasonicSensor1 connected.
 Pioneer_p3dx_ultrasonicSensor2 connected.
 Pioneer_p3dx_ultrasonicSensor3 connected.
 Pioneer_p3dx_ultrasonicSensor4 connected.
 Pioneer_p3dx_ultrasonicSensor5 connected.
 Pioneer_p3dx_ultrasonicSensor6 connected.
 Pioneer_p3dx_ultrasonicSensor7 connected.
 Pioneer_p3dx_ultrasonicSensor8 connected.
 Pioneer_p3dx_ultrasonicSensor9 connected.
 Pioneer_p3dx_ultrasonicSensor10 connected.
 Pioneer_p3dx_ultrasonicSensor11 connected.
 Pioneer_p3dx_ultrasonicSensor12 connected.
 Pioneer_p3dx_ultrasonicSensor13 connected.
 Pioneer_p3dx_ultrasonicSensor14 connected.
 Pioneer_p3dx_ultrasonicSensor15 connected.
 Pioneer_p3dx_ultrasonicSensor16 connected.
 Vision sensor connected.
 Laser connected.
 Left motor connected.
 Right motor connected.
 Robot connected.
[-6.61632545560121, 6.61632545560121]
[-1.3015722207740086, 1.3015722207740086]
[-1.4100365725051758, 1.4100365725051758]
[-1.5185009242363432, 1.5185009242363432]
[

[-95.01477211650062, 95.01477211650062]
[-95.12323646823178, 95.12323646823178]
[-95.23170081996295, 95.23170081996295]
[-95.34016517169411, 95.34016517169411]
[-95.44862952342527, 95.44862952342527]
[-95.55709387515644, 95.55709387515644]
[-95.6655582268876, 95.6655582268876]
[-95.77402257861877, 95.77402257861877]
[-95.88248693034993, 95.88248693034993]
[-95.99095128208108, 95.99095128208108]
[-96.09941563381226, 96.09941563381226]
[-96.20787998554341, 96.20787998554341]
[-96.31634433727459, 96.31634433727459]
[-96.42480868900574, 96.42480868900574]
[-96.5332730407369, 96.5332730407369]
[-96.64173739246807, 96.64173739246807]
[-96.75020174419923, 96.75020174419923]
[-96.8586660959304, 96.8586660959304]
[-96.96713044766156, 96.96713044766156]
[-97.07559479939272, 97.07559479939272]
[-97.18405915112389, 97.18405915112389]
[-97.29252350285505, 97.29252350285505]
[-97.40098785458622, 97.40098785458622]
[-97.50945220631738, 97.50945220631738]
[-97.61791655804853, 97.61791655804853]
[-97.7

[-168.01146996848144, 168.01146996848144]
[-168.11993461527797, 168.11993461527797]
[-168.22839926207448, 168.22839926207448]
[-168.336863908871, 168.336863908871]
[-168.44532855566754, 168.44532855566754]
[-168.55379320246408, 168.55379320246408]
[-168.6622578492606, 168.6622578492606]
[-168.77072249605712, 168.77072249605712]
[-168.87918714285365, 168.87918714285365]
[-168.9876517896502, 168.9876517896502]
[-169.09611643644672, 169.09611643644672]
[-169.20458108324326, 169.20458108324326]
[-169.31304573003976, 169.31304573003976]
[-169.4215103768363, 169.4215103768363]
[-169.52997502363283, 169.52997502363283]
[-169.63843967042936, 169.63843967042936]
[-169.7469043172259, 169.7469043172259]
[-169.8553689640224, 169.8553689640224]
[-169.96383361081894, 169.96383361081894]
[-170.07229825761547, 170.07229825761547]
[-170.180762904412, 170.180762904412]
[-170.28922755120854, 170.28922755120854]
[-170.39769219800505, 170.39769219800505]
[-170.50615684480158, 170.50615684480158]
[-170.6146

[-246.24926385814476, 246.24926385814476]
[-246.35731073947287, 246.35731073947287]
[-246.46535762080097, 246.46535762080097]
[-246.5734045021291, 246.5734045021291]
[-246.68145138345722, 246.68145138345722]
[-246.78949826478535, 246.78949826478535]
[-246.89754514611346, 246.89754514611346]
[-247.00559202744157, 247.00559202744157]
[-247.1136389087697, 247.1136389087697]
[-247.2216857900978, 247.2216857900978]
[-247.32973267142594, 247.32973267142594]
[-247.43777955275405, 247.43777955275405]
[-247.54582643408216, 247.54582643408216]
[-247.6538733154103, 247.6538733154103]
[-247.7619201967384, 247.7619201967384]
[-247.86996707806654, 247.86996707806654]
[-247.97801395939464, 247.97801395939464]
[-248.08606084072275, 248.08606084072275]
[-248.1941077220509, 248.1941077220509]
[-248.302154603379, 248.302154603379]
[-248.41020148470713, 248.41020148470713]
[-248.51824836603524, 248.51824836603524]
[-248.62629524736334, 248.62629524736334]
[-248.73434212869148, 248.73434212869148]
[-248.84

[-327.0127102579491, 327.0127102579491]
[-327.1195120196785, 327.1195120196785]
[-327.2263137814079, 327.2263137814079]
[-327.33311554313724, 327.33311554313724]
[-327.43991730486664, 327.43991730486664]
[-327.54671906659604, 327.54671906659604]
[-327.65352082832544, 327.65352082832544]
[-327.76032259005484, 327.76032259005484]
[-327.8671243517842, 327.8671243517842]
[-327.9739261135136, 327.9739261135136]
[-328.080727875243, 328.080727875243]
[-328.1875296369724, 328.1875296369724]
[-328.2943313987018, 328.2943313987018]
[-328.40113316043113, 328.40113316043113]
[-328.50793492216053, 328.50793492216053]
[-328.61473668388993, 328.61473668388993]
[-328.72153844561933, 328.72153844561933]
[-328.82834020734873, 328.82834020734873]
[-328.9351419690781, 328.9351419690781]
[-329.0419437308075, 329.0419437308075]
[-329.1487454925369, 329.1487454925369]
[-329.2555472542663, 329.2555472542663]
[-329.3623490159957, 329.3623490159957]
[-329.469150777725, 329.469150777725]
[-329.5759525394544, 329

...

[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300

[3.300717723119589, 3.300717723119589]
[3.300717723119589, 3.300717723119589]
[3.2938719779662486, 3.2938719779662486]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322,

[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940322, 3.2995767655940322]
[3.2995767655940

[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909782, 3.2984487711909782]
[3.2984487711909

[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996164, 3.2973386846996164]
[3.2973386846996

In [ ]:
if(len(path) > 0):
    path = np.array(path)
    path_odometry = np.array(path_odometry)

    difx = path[1,0] - path_odometry[1,0]
    dify = path[1,1] - path_odometry[1,1]
    path_odometry[:,0] = path_odometry[:,0]+difx
    path_odometry[:,1] = path_odometry[:,1]+dify

    plot_odometry_vs_GT(path, path_odometry)